In [1]:
! pip install bedrock-ge folium mapclassify marimo --quiet

In [ ]:
import io
import platform
import sys
import zipfile

import chardet
import geopandas as gpd
import marimo as mo
import pandas as pd
import requests
from pyproj import CRS

from bedrock_ge.gi.ags.read import ags_to_dfs
from bedrock_ge.gi.ags.transform import ags3_db_to_no_gis_brgi_db
from bedrock_ge.gi.concatenate import concatenate_databases
from bedrock_ge.gi.gis_geometry import calculate_gis_geometry
from bedrock_ge.gi.validate import check_brgi_database, check_no_gis_brgi_database
from bedrock_ge.gi.write import write_gi_db_to_gpkg

print(platform.system())
print(sys.version)
print(sys.executable)

Windows
3.9.20 (main, Sep  9 2024, 20:47:28) [MSC v.1929 64 bit (AMD64)]
c:\Users\joost\ReposWindows\bedrock-ge\.venv\Scripts\python.exe


In [ ]:
def zip_of_ags3s_to_bedrock_gi_database(zip, crs):
    """Read AGS 3 files from a ZIP archive and convert them to a dictionary of pandas dataframes."""
    brgi_db = {}
    with zipfile.ZipFile(zip) as zip_ref:
        # Iterate over files and directories in the .zip archive
        for file_name in zip_ref.namelist():
            # Only process files that have an .ags or .AGS extension
            if file_name.lower().endswith(".ags"):
                print(f"\n🖥️ Processing {file_name} ...")
                with zip_ref.open(file_name) as ags3_file:
                    ags3_data = ags3_file.read()
                    detected_encoding = chardet.detect(ags3_data)["encoding"]
                    ags3_data = ags3_data.decode(detected_encoding)
                # Convert content of a single AGS 3 file to a Dictionary of pandas dataframes (a database)
                ags3_db = ags_to_dfs(ags3_data)
                report_no = file_name.split("/")[0]
                ags3_db["PROJ"]["REPORT_NO"] = int(report_no)
                project_uid = f"{ags3_db['PROJ']['PROJ_ID'].iloc[0]}_{file_name}"
                ags3_db["PROJ"]["project_uid"] = project_uid
                # Remove (Static) CPT AGS 3 group 'STCN' from brgi_db, because CPT data processing needs to be reviewed.
                # Not efficient to create a GIS point for every point where a CPT measures a value.
                if "STCN" in ags3_db.keys():
                    del ags3_db["STCN"]
                # Create GI data tables with bedrock-ge names and add columns (project_uid, location_uid, sample_uid),
                # such that data from multiple AGS files can be combined
                brgi_db_from_1_ags3_file = ags3_db_to_no_gis_brgi_db(ags3_db, crs)
                print(
                    f"🧐 Validating the Bedrock GI database from AGS file {file_name}..."
                )
                check_no_gis_brgi_database(brgi_db_from_1_ags3_file)
                print(
                    f"\n✅ Succesfully converted {file_name} to Bedrock GI database and validated!\n"
                )
                print(
                    f"🧵 Concatenating Bedrock GI database for {file_name} to existing Bedrock GI database...\n"
                )
                brgi_db = concatenate_databases(brgi_db, brgi_db_from_1_ags3_file)

                # Drop all rows that have completely duplicate rows in the Project table
                brgi_db["Project"] = brgi_db["Project"].drop_duplicates()
                # Then drop all that unfortunately still have a duplicate project_uid
                brgi_db["Project"] = brgi_db["Project"].drop_duplicates(
                    subset="project_uid", keep="first"
                )
    return brgi_db


# AGS 3 Data in Kai Tak, Hong Kong

This notebook demonstrates how to:

1. Use `bedrock-ge` to load Ground Investigation (GI) data from AGS 3 files (a common GI data format in Hong Kong)
2. Convert the AGS 3 data into a standardized GI database using `bedrock-ge`
3. Transform the GI data into 3D GIS features with proper coordinates and geometry ([OGC Simple Feature Access](https://en.wikipedia.org/wiki/Simple_Features))
4. Explore and analyze the GI data using:
   - Interactive filtering with Pandas dataframes
   - Visualization on interactive maps with GeoPandas
5. Export the processed GI database to a GeoPackage file for use in GIS software

We'll work with real GI data from the Kai Tak neighborhood in Hong Kong.

## Context

Kai Tak is a neighborhood in Kowloon, Hong Kong. One of the highlights of Kai Tak used to be its airport. It holds a special place in aviation history due to its unique and challenging approach, which involved pilots making a steep descent over a densely populated area while making a sharp turn at the same time and then landing on a single runway that jutted out into Victoria Harbor. [Landing at Kai Tak Airport | YouTube](https://www.youtube.com/watch?v=OtnL4KYVtDE)

In 1998, the new Hong Kong International Airport opened, and operations at Kai Tak Airport were ceased. After the closure, the former Kai Tak Airport and surrounding neighborhood underwent a massive redevelopment project to transform it into a new residential and commercial district, which is still continuing today.

Have a look at the [Kai Tak Speckle Project](https://app.speckle.systems/projects/013aaf06e7/models/0e43d1f003,a739490298) to get an idea what Kai Tak looks like now. (Developments are going fast, so [Google Maps 3D](https://www.google.com/maps/@22.3065043,114.2020499,462a,35y,343.1h,75.5t/data=!3m1!1e3?entry=ttu) is a bit outdated.)

## The Kai Tak AGS 3 ground investigation data

Ground Investigation Data for all of Hong Kong can be found here:
[GEO Data for Public Use](https://www.ginfo.cedd.gov.hk/GEOOpenData/eng/Default.aspx) → [Ground Investigation (GI) and Laboratory Test (LT) Records](https://www.ginfo.cedd.gov.hk/GEOOpenData/eng/GI.aspx)

The Ground Investigation data specific to the Kai Tak neighborhood in Hong Kong can be found in the `bedrock-ge` GitHub repository:
[`github.com/bedrock-engineer/bedrock-ge/examples/hk_kaitak_ags3/kaitak_ags3.zip`](https://github.com/bedrock-engineer/bedrock-ge/blob/main/examples/hk_kaitak_ags3/kaitak_ags3.zip).
This archive contains GI data from 88 AGS 3 files, with a total of 834 locations (boreholes and Cone Penetration Tests).

One of the AGS 3 files with GI data was left outside the ZIP archive, such that you can have a look at the structure of an AGS 3 file:
[`github.com/bedrock-engineer/bedrock-ge/examples/hk_kaitak_ags3/ASD012162 AGS.ags`](https://github.com/bedrock-engineer/bedrock-ge/blob/main/examples/hk_kaitak_ags3/64475_ASD012162%20AGS.ags)

### Getting the AGS 3 files

To make it easy to run this notebook on your computer (locally) in the browser (remotely) in [marimo.app](https://marimo.app/) or [Google Colab](https://colab.research.google.com/), the code below requests the ZIP archive from GitHub and directly processes it. However, you can also download the ZIP from GitHub (link above) or directly from this notebook [by clicking this raw.githubusercontent.com raw url [ ↓ ]](http://raw.githubusercontent.com/bedrock-engineer/bedrock-ge/main/examples/hk_kaitak_ags3/kaitak_ags3.zip).

The cell below works as is, but has a commented line 2, to help you in case you have downloaded the ZIP, and want to use that downloaded ZIP in this notebook.

In [4]:
# Read ZIP from disk after downloading manually
# zip = Path(r"C:\Users\joost\ReposWindows\bedrock-ge\examples\hk_kaitak_ags3\public\kaitak_ags3.zip")

# Request ZIP from GitHub
raw_githubusercontent_url = "https://raw.githubusercontent.com/bedrock-engineer/bedrock-ge/main/examples/hk_kaitak_ags3/kaitak_ags3.zip"
zip = io.BytesIO(requests.get(raw_githubusercontent_url).content)

## Converting the AGS 3 files to a relational database

A relational database is a database with multiple tables that are linked to each other with relations. This type of database is ideal for storing  GI data, given its hierarchical structure:

```
Project
 └───Location
      ├───InSitu_TEST
      └───Sample
          └───Lab_TEST
```

Where `Project`, `Location`, `InSitu_TEST`, `Sample` and `Lab_TEST` are all tables that are linked to each other with the hierarchical structure shown above, meaning that all relations are many-to-one:

- Each GI location (many) is related to one project.
- Each sample or in-situ test (many) is related to one GI location.
- Each lab test is related to one sample.

In Python it's convenient to represent a relational database as a dictionary of dataframe's.

### Converting AGS 3 files to a dictionary of dataframes

The AGS 3 files can be converted to a dictionary of dataframes using the function `list_of_ags3s_to_bedrock_gi_database(ags3_file_paths, CRS)`. The result is shown below. Have a look at the different tables and the data in those tables. Make sure to use the search and filter functionality to explore the data if you're using marimo to run this notebook!

Notice the additional columns that were added to the tables by `bedrock-ge`:

- To make sure that the primary keys of the GI data tables are unique when putting data from multiple AGS files together:
    `project_uid`, `location_uid`, `sample_uid`
- To make it possible to generate 3D GIS geometry for the `Location`, `Sample` and `InSitu_TEST` tables:
    In the `Location` table: `easting`, `northing`, `ground_level_elevation`, `depth_to_base`
  In the `Sample` and `InSitu_TEST` tables: `depth_to_top` and, in case the test or sample is taken over a depth interval, `depth_to_base`.

In [5]:
brgi_db = zip_of_ags3s_to_bedrock_gi_database(zip, CRS("EPSG:2326"))

# Some ISPT_NVAL (SPT count) are not numeric, e.g. "100/0.29"
# When converting to numeric, these non-numeric values are converted to NaN
brgi_db["InSitu_ISPT"]["ISPT_NVAL"] = pd.to_numeric(
    brgi_db["InSitu_ISPT"]["ISPT_NVAL"], errors="coerce"
)


🖥️ Processing 21659/9508008.AGS ...

🚨 CAUTION: The number of columns on line 70 (2) doesn't match the number of columns of group DREM (3)!
DREM headers: ['HOLE_ID', 'DREM_DPTH', 'DREM_REM']
Line 70:      ['"MBH36/01', '57.35   (200 / 70mm)"']

AGS 3 data was read for Project GE/95/08.8
This Ground Investigation data contains groups:
['PROJ', 'HDIA', 'DREM', 'PTIM', 'SAMP', 'FRAC', 'CORE', 'ISPT', 'HOLE', 'IVAN', 'GEOL', 'WETH', 'DETL']

Transforming AGS 3 groups to Bedrock tables...
Transforming AGS 3 group 'PROJ' to Bedrock GI 'Project' table...
Transforming AGS 3 group 'HOLE' to Bedrock GI 'Location' table...
Transforming AGS 3 group 'SAMP' to Bedrock GI 'Sample' table...
Transforming AGS 3 group 'HDIA' to Bedrock GI 'InSitu_HDIA' table...
Transforming AGS 3 group 'DREM' to Bedrock GI 'InSitu_DREM' table...
Transforming AGS 3 group 'PTIM' to Bedrock GI 'InSitu_PTIM' table...
Transforming AGS 3 group 'FRAC' to Bedrock GI 'InSitu_FRAC' table...
Transforming AGS 3 group 'CORE' to Bedr

In [6]:
sel_brgi_table = mo.ui.dropdown(brgi_db, value="Project")
mo.md(f"Select the Bedrock GI table you want to explore: {sel_brgi_table}")

_md()

In [7]:
sel_brgi_table.value

PROJ_ID                                          PROJ_NAME  \
0       GE/95/08.8  SOUTH EAST KOWLOON DEVELOPMENT FEASIBILITY STU...   
1      GE/95/08.10  SOUTH EAST KOWLOON DEVELOPMENT FEASIBILITY STU...   
2      GE/95/08.10                   S.E. Kowloon Development Phase 2   
3      GE/95/08.10                   S.E. Kowloon Development Phase 2   
4      GE/95/08.10                   S.E. Kowloon Development Phase 2   
..             ...                                                ...   
83  GE/2010/02.50A  Agreement No. CE 43/2010 (HY) Central Kowloon ...   
84   GE/2010/02.50  Agreement No. CE 43/2010 (HY) Central Kowloon ...   
85  GE/2013/04.18A  Ground Investigation - Urban (Term Contract), ...   
86  GE/2013/04.18A  Ground Investigation - Urban (Term Contract), ...   
87           J3573  Multi-Purpose Complex (MPSC) at Kai Tak, Kowlo...   

                                        PROJ_LOC  \
0   INVESTIGATION- PHASE I SI (ADDITIONAL WORKS)   
1                                            NaN   
2                                    Kowloon Bay   
3                                    Kowloon Bay   
4                                    Kowloon Bay   
..                                           ...   
83                                           NaN   
84                                           NaN   
85                                           NaN   
86                                           NaN   
87                Kai Tak, Kowloon City District   

                                            PROJ_CLNT  \
0                                      PM/KOWLOON TDD   
1                                  PM / KOWLOON - TDD   
2                    Territory Development Department   
3                    Territory Development Department   
4                    Territory Development Department   
..                                                ...   
83  HKSAR - Civil Engineering & Development Depart...   
84  HKSAR - Civil Engineering & Development Depart...   
85  Civil Engineering and Development Department, ...   
86  Civil Engineering and Development Department, ...   
87                  ARCHITECTURAL SERVICES DEPARTMENT   

                               PROJ_CONT                           PROJ_ENG  \
0                 BACHY SOLETANCHE GROUP                           MAUNSELL   
1                 BACHY SOLETANCHE GROUP                           MAUNSELL   
2   Fugro Geotechnical Services (HK) Ltd      Maunsell Consultants Asia Ltd   
3   Fugro Geotechnical Services (HK) Ltd      Maunsell Consultants Asia Ltd   
4   Fugro Geotechnical Services (HK) Ltd      Maunsell Consultants Asia Ltd   
..                                   ...                                ...   
83           GAMMON CONSTRUCTION LIMITED                                NaN   
84           GAMMON CONSTRUCTION LIMITED  Arup-Mott MacDonald Joint Venture   
85      DrilTech Ground Engineering Ltd.   Mott MacDonald Hong Kong Limited   
86      DrilTech Ground Engineering Ltd.   Mott MacDonald Hong Kong Limited   
87           GAMMON CONSTRUCTION LIMITED                                NaN   

   PROJ_MEMO   PROJ_DATE PROJ_AGS  REPORT_NO  \
0   GE/95/08    15/05/96    07/94      21659   
1   GE/95/08   29/6/1996    07/94      21761   
2   GE/95/08    04.06.96     7.94      21761   
3   GE/95/08    04.06.96     7.94      21761   
4   GE/95/08    04.06.96     7.94      21761   
..       ...         ...      ...        ...   
83       NaN  20/02/2012        3      54941   
84       NaN  02/04/2012        3      55191   
85       NaN  24/01/2014        3      58357   
86       NaN  24/01/2014        3      58358   
87       NaN  26/01/2017        3      64475   

                               project_uid  \
0             GE/95/08.8_21659/9508008.AGS   
1            GE/95/08.10_21761/9508010.AGS   
2             GE/95/08.10_21761/MCP141.AGS   
3             GE/95/08.10_21761/MCP221.AGS   
4             GE/95/08.10_21761/MCP231.AGS   
..                    

## Relational database to 3D geospatial database
A geospatial database is a relational database that has been enhanced to store geospatial data. There are two broad categories of geospatial data:

1. [Raster data](https://en.wikipedia.org/wiki/GIS_file_format#Raster_formats): geographic information as a grid of pixels (cells), where each pixel stores a value corresponding to a specific location and attribute, such as elevation, temperature, or land cover. So, a Digital Elevation Model (DEM) is an example of GIS raster data.
2. [Vector data](https://en.wikipedia.org/wiki/GIS_file_format#Vector_formats): tables in which each row contains:
    - [Simple feature GIS geometry](https://en.wikipedia.org/wiki/Simple_Features), represented as [Well-Known Text](https://en.wikipedia.org/wiki/Well-known_text_representation_of_geometry). For example in the `InSitu_GEOL` and `InSitu_ISPT` tables:
        `InSitu_GEOL`: a depth interval in a borehole where sand was found.
        `InSitu_ISPT`: a point in a borehole where an SPT test was performed.
    - Attributes that describe the GIS geometry. For example in the `InSitu_GEOL` and `InSitu_ISPT` tables:
        `InSitu_GEOL`: the geology code (`GEOL_GEOL`), general description of stratum (`GEOL_DESC`), etc.
        `InSitu_ISPT`: the SPT N-value (`ISPT_NVAL`), energy ratio of the hammer (`ISPT_ERAT`), etc.

So, when representing GI data as 3D GIS features, we are talking about GIS vector data.

### From GI dataframe to `geopandas.GeoDataFrame`

In order to construct the 3D simple feature GIS geometry of the `Location`s, `Sample`s and `InSitu_TEST`s, a few more columns have to be calcualated for each of these tables: `elevation_at_top` and `elevation_at_base` if the in-situ test or sample was taken over a depth interval.

The 3D simple feature GIS geometry as [WKT](https://en.wikipedia.org/wiki/Well-known_text_representation_of_geometry) for point tests and samples:
`POINT (easting northing elevation_at_top)`

The 3D simple feature GIS geometry as WKT for in-situ tests and samples taken over a depth interval:
`LINESTRING (easting northing elevation_at_top, easting northing elevation_at_base)`

Additionally, a `LonLatHeight` table is created which contains the GI locations at ground level in WGS84 - World Geodetic System 1984 - EPSG:4326 coordinates (Longitude, Latitude, Ellipsoidal Height), which in WKT looks like:
`POINT (longitude latitude wgs84_ground_level_height)`

The reason for creating the `LonLatHeight` table is that vertical lines in projected Coordinate Reference Systems (CRS) are often not rendered nicely by default in all web-mapping software. Vertical lines are often not visible when looking at a map from above, and not all web-mapping software is capable of handling geometry in non-WGS84, i.e. (Lon, Lat) coordinates.

In [8]:
brgi_geodb = calculate_gis_geometry(brgi_db)
check_brgi_database(brgi_geodb)

Calculating GIS geometry for the Bedrock GI database tables...
Calculating GIS geometry for the Bedrock GI 'Location' table...
Creating 'LonLatHeight' table with GI locations in WGS84 geodetic coordinates...
    WGS84 geodetic coordinates: (Longitude, Latitude, Ground Level Ellipsoidal Height)
Calculating GIS geometry for the Bedrock GI 'Sample' table...
Calculating GIS geometry for the Bedrock GI 'InSitu_HDIA' table...
Calculating GIS geometry for the Bedrock GI 'InSitu_DREM' table...
Calculating GIS geometry for the Bedrock GI 'InSitu_PTIM' table...
Calculating GIS geometry for the Bedrock GI 'InSitu_FRAC' table...
Calculating GIS geometry for the Bedrock GI 'InSitu_CORE' table...
Calculating GIS geometry for the Bedrock GI 'InSitu_ISPT' table...
Calculating GIS geometry for the Bedrock GI 'InSitu_IVAN' table...
Calculating GIS geometry for the Bedrock GI 'InSitu_GEOL' table...
Calculating GIS geometry for the Bedrock GI 'InSitu_WETH' table...
Calculating GIS geometry for the Bedrock

True

## Ground Investigation data exploration

After creating the Bedrock GI 3D Geospatial Database `brgi_geodb` - which is a dictionary of [`geopandas.GeoDataFrame`](https://geopandas.org/en/stable/docs/reference/api/geopandas.GeoDataFrame.html#geopandas.GeoDataFrame)s - you can explore the Kai Tak Ground Investigation data on an interactive map by applying the [`geopandas.GeoDataFrame.explore()`](https://geopandas.org/en/stable/docs/reference/api/geopandas.GeoDataFrame.explore.html#geopandas.GeoDataFrame.explore) method to the different tables in the `brgi_geodb`.

Do note that this works best on the tables with `POINT` GIS geometry such as `LonLatHeight` or `InSitu_ISPT`. Tables with vertical `LINESTRING` GIS geometry, such as `Location`, `InSitu_GEOL` or `InSitu_WETH`, display very small on the `gdf.explore()` `leaflet`-based interactive map, and don't show at all on the `matplotlib`-based `gdf.plot()`.

In [9]:
brgi_geodb["LonLatHeight"].explore()

With marimo's built-in data exploration tables and dataframes, it's also really easy to filter and visualize the GI data.

For example, in the `InSitu_ISPT` table (SPT data) you could apply a filter to the `ISPT_NVAL` (SPT N-value) of e.g. 1 - 10. When you then select those rows and then scroll to the map below, you'll see all the locations where soft soils were encountered.

In [10]:
explore_brgi_table = mo.ui.dropdown(brgi_db, value="InSitu_ISPT")
mo.md(f"Select the GI table you want to explore: {explore_brgi_table}")

_md()

In [11]:
filtered_table = mo.ui.table(explore_brgi_table.value)
filtered_table

table()

In [ ]:
def gi_exploration_map(filtered_brgi_table):
    if "location_uid" not in filtered_brgi_table.value.columns:
        output = mo.md(
            "No interactive map with the data selected in the table above can be shown, because the you're exploring isn't linked to the `LonLatHeight` table with a `location_uid` column, i.e. doesn't have `location_uid` as a foreign key."
        ).callout("warn")
    else:
        filtered_df = filtered_brgi_table.value.merge(
            brgi_geodb["LonLatHeight"], on="location_uid", how="inner"
        )
        filtered_gdf = gpd.GeoDataFrame(
            filtered_df,
            geometry=filtered_df["geometry"],
            crs="EPSG:4326",  # 4326 is the WGS84 (lon, lat) EPSG code
        )
        output = filtered_gdf.explore()
    return output


gi_exploration_map(filtered_table)

C:\Users\joost\AppData\Local\Temp\ipykernel_7116\761422290.py:15: UserWarning: The GeoSeries you are attempting to plot is composed of empty geometries. Nothing has been displayed.
  output = filtered_gdf.explore()


Something else you might be interested in, is where the weathering grade of the soil or rock is low. Weathering grades range from `I` (Fresh Rock) to `VI` (Residual Soil). All rock with a weathering grade of `III` (Moderately Decomposed) or better is still considered competent rock.

The weathering grades can be found in the `WETH_GRAD` column in the `InSitu_WETH` table (Weathering data). Therefore, to find all competent rock, we need to filter out all the rows that contain a `V`, which you can do in the widget below.

That widget also shows the Python code that creates the filter:

```python
df_next = df
df_next = df_next[~((df_next["WETH_GRAD"].str.contains("V")))]
```

In [13]:
explore_brgi_df = mo.ui.dropdown(brgi_db, value="InSitu_WETH")
mo.md(f"Select the GI table you want to explore: {explore_brgi_df}")

_md()

In [14]:
filtered_df = mo.ui.dataframe(explore_brgi_df.value)
filtered_df

dataframe()

In [15]:
gi_exploration_map(filtered_df)

## Saving the GI geospatial database as a GeoPackage (.gpkg)

Finally, lets write, i.e. persist `brgi_geodb` - a Python dictionary of `geopandas.GeoDataFrames` - to an actual geospatial database file, so we can share our GI data with others.
For example, to reuse it in other notebooks, create dashboards, access the GI data in QGIS or ArcGIS, and more...

A GeoPackage is an OGC-standardized extension of SQLite (a relational database in a single file, .sqlite or .db) that allows you to store any type of GIS data (both raster as well as vector data) in a single file that has the .gpkg extension. Therefore, many (open-source) GIS software packages support GeoPackage!

> [What about Shapefile and GeoJSON?](#what-about-shapefile-and-geojson)

In [16]:
output = None
if platform.system() != "Emscripten":
    write_gi_db_to_gpkg(brgi_geodb, mo.notebook_dir() / "kaitak_gi.gpkg")
else:
    output = mo.md(
        "Writing a GeoPackage from WebAssembly (marimo playground) causes geopandas to think that the GeoDataFrames in the `brgi_geodb` don't have a geometry column. You can [download the GeoPackage from GitHub](https://github.com/bedrock-engineer/bedrock-ge/blob/main/examples/hk_kaitak_ags3/kaitak_gi.gpkg)"
    ).callout("warn")
output

Table names shouldn't contain [':', '/', '\\', '?', '*', '[', ']'] or spaces and shouldn't be longer than 31 characters.
 Replaced '?LEGD' with 'LEGD'.
Ground Investigation data has been written to 'c:\Users\joost\ReposWindows\bedrock-ge\examples\hk_kaitak_ags3\kaitak_gi.gpkg'.


## What's next?

As mentioned above, the `kaitak_gi.gpkg` GeoPackage can be loaded into QGIS or ArcGIS. QGIS and ArcGIS have [connectors for the Speckle platform](https://www.speckle.systems/connectors), which allows you to publish GIS data to Speckle.

With the Speckle viewer you can visualize the GI data in context with data from other AEC software such as Civil3D (Click the balloon!):

<iframe title="Speckle" src="https://app.speckle.systems/projects/013aaf06e7/models/1cbe68ed69,44c8d1ecae,9535541c2b,a739490298,ff81bfa02b#embed=%7B%22isEnabled%22%3Atrue%7D" width="100%" height="400" frameborder="0"></iframe>

Additionally, you can load the GI data in other software that Speckle has a connector for, such as Rhino / Grasshopper to enable parameteric geotechnical engineering workflows.

## What about Shapefile and GeoJSON?

### Shapefile

Bluntly put, Shapefile is a bad format.

Among other problems, Shapefile isn't just a single file. One has to at least share three files [(*.shp, *.dbf, *.shx)](https://en.wikipedia.org/wiki/Shapefile#Mandatory_files), which doesn't include the definition of a CRS. In case that doesn't sound terrible enough to you yet, please have a look at the fantastic website [switchfromshapefile.org](http://switchfromshapefile.org/).

### GeoJSON

GeoJSON is a nice, human readable file format for GIS vector data, which is especially useful for web services, but has a few drawbacks:

- Although it is technically possible to use GeoJSON with more CRSs, the [specification states clearly](https://tools.ietf.org/html/rfc7946#section-4) that WGS84, with EPSG:4326 and coordinates (Lon, Lat, Height), is the only CRS that should be used in GeoJSON (see [switchfromshapefile.org](http://switchfromshapefile.org/#geojson)).
- GeoJSON support in ArcGIS isn't fantastic. You have to go through [Geoprocessing - JSON to Features conversion tool](https://pro.arcgis.com/en/pro-app/latest/tool-reference/conversion/json-to-features.htm) to add a GeoJSON to your ArcGIS project, which is a bit cumbersome.